In [50]:
import json
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC
from sklearn.metrics import classification_report
from sklearn.ensemble import RandomForestClassifier

data = []
with open('train.json', 'r', encoding='utf-8') as file:
    for line in file:
        data.append(json.loads(line))


In [24]:
import random

merged = []

for d in data:
    for p in d['passages']:
        merged.extend(p['exhaustivelyAnnotatedProperties'])

print(len(merged))
print(merged[0])


7254
{'propertyId': '9', 'propertyName': 'EDUCATED_AT', 'propertyDescription': 'Describes the relationship between a person and the institution where she/he studied.'}


In [12]:
import pandas as pd

factes_df = pd.DataFrame(merged)


NameError: name 'merged' is not defined

In [31]:
factes_df = factes_df.drop_duplicates().sort_values('propertyId')


In [32]:
factes_df


propertyId           propertyName  \
1           1          SUBSIDIARY_OF   
3          10            NATIONALITY   
24         11     PLACE_OF_RESIDENCE   
33         12         PLACE_OF_BIRTH   
2          14          DATE_OF_DEATH   
35         15          DATE_OF_BIRTH   
11          2             FOUNDED_BY   
12         25                 SPOUSE   
19          3  EMPLOYEE_OR_MEMBER_OF   
39         34               CHILD_OF   
5           4                    CEO   
32         45  POLITICAL_AFFILIATION   
21          5           DATE_FOUNDED   
6           6           HEADQUARTERS   
0           9            EDUCATED_AT   

                                  propertyDescription  
1   Describes the relationship between a parent co...  
3   Describes he country of a person's citizenship...  
24  Describes the relationship between a person an...  
33  Describes the relationship between a person an...  
2            Describes the date of death of a person.  
35           Describes the date of birth of a person.  
11  Describes the relationship between an organiza...  
12  Describes the relationship between a person an...  
19  Describes the previous/current employer of a p...  
39  Describes the relationship between a person an...  
5   Describes the relationship between an organiza...  
32  Describes the relationship between a person an...  
21          Describes the founding date of a company.  
6   Describes the specific location where an organ...  
0   Describes the relationship between a person an...

In [33]:
factes_df.to_csv('dsr_rasa_bot/data/relations.csv', index=False)


In [11]:
data[2]


{'fold': 1,
 'source': 'Diffbot Knowledge Graph',
 'documentId': '29726',
 'documentText': 'Morphine\n\nMorphine was an American alternative rock group formed by Mark Sandman, Dana Colley, and Jerome Deupree in Cambridge, Massachusetts in 1989. After five successful albums and extensive touring, they disbanded after lead vocalist Sandman died of a heart attack onstage in Palestrina, Italy, on July 3, 1999. Founding members have reformed into the band Vapors of Morphine, maintaining much of the original style and sound.',
 'passages': [{'passageId': '29726:151:315',
   'exhaustivelyAnnotatedProperties': [{'propertyId': '14',
     'propertyName': 'DATE_OF_DEATH',
     'propertyDescription': 'Describes the date of death of a person.'}],
   'passageStart': 151,
   'passageEnd': 315,
   'passageText': 'After five successful albums and extensive touring, they disbanded after lead vocalist Sandman died of a heart attack onstage in Palestrina, Italy, on July 3, 1999.',
   'facts': [{'factId': 

In [47]:
txt_pra = []
for d in data:
    if '\n\n' in d['documentText']:
        txt_pra.append(d['documentText'].split('\n\n'))

print((txt_pra))


[['Documents Assist', "Florida Cheap Divorce - Simple Divorce $280 flat fee - No Court Divorce\nEstablished in 2006.\nAfter a few years working as an Independent Associate of Legal Shield, formerly known as Pre-Paid Legal, Yamil Fuentes made it her mission to help her clients take advantage of their access to the legal system. After going through her own personal divorce she realized there was a need of affordable divorce services in the State of Florida.\nWhen she founded Apex Legal Document Preparation Services she became a Premium Member of the FALDP (Florida Association of Legal Document Preparers) and educated herself on the different types of divorce been offered across the State of Florida and learned from the best in the industry of legal document preparation services.\nThrough her membership she embarked on a journey to learn how to make the divorce process as easy as possible for her clients, making her company the most sought after divorce preparer in Florida touting the fol

In [84]:
import pandas as pd

relations_df = pd.read_csv('dsr_rasa_bot/data/relations.csv')


In [86]:
relations_map = {k[0]: k for k in relations_df.values}
relations_map


{1: array([1, 'SUBSIDIARY_OF',
        'Describes the relationship between a parent company and one of its subsidiaries.'],
       dtype=object),
 10: array([10, 'NATIONALITY',
        "Describes he country of a person's citizenship or country in which the person is deemed a national."],
       dtype=object),
 11: array([11, 'PLACE_OF_RESIDENCE',
        'Describes the relationship between a person and the location where she/he lives/lived.'],
       dtype=object),
 12: array([12, 'PLACE_OF_BIRTH',
        'Describes the relationship between a person and the location where she/he was born.'],
       dtype=object),
 14: array([14, 'DATE_OF_DEATH', 'Describes the date of death of a person.'],
       dtype=object),
 15: array([15, 'DATE_OF_BIRTH', 'Describes the date of birth of a person.'],
       dtype=object),
 2: array([2, 'FOUNDED_BY',
        'Describes the relationship between an organization and its founder or co-founder.'],
       dtype=object),
 25: array([25, 'SPOUSE',
        

In [82]:
relations_scope = [relations_map[r.split(" ")[0]][0] for r in """DATE_OF_BIRTH (PER–DATE)
PLACE_OF_RESIDENCE (PER–LOC) 
PLACE_OF_BIRTH (PER–LOC)
NATIONALITY (PER–LOC)
EMPLOYEE_OR_MEMBER_OF (PER–ORG) 
EDUCATED_AT (PER–ORG) """.split('\n')]
# relations_scope.sort()
relations_scope


[15, 11, 12, 10, 3, 9]

In [80]:
data_with_facts = []
all_facts = []
print(f'Original document count = {len(data)}')
for d in data:
    passages_with_facts = []
    for p in d['passages']:
        facts = []
        for f in p['facts']:
            if int(f['propertyId']) in relations_scope and str(f['subjectText']).lower() not in ['i', 'my', 'he', 'she', 'his', 'her', 'who', 'myself'] and str(f['objectText']).lower() not in ['where', 'them', 'they', 'when']:
                facts.append(f)
                all_facts.append(f)
        p['facts'] = facts
        # print(len(p['facts']))
        if len(p['facts']) > 0:
            passages_with_facts.append(p)
    d['passages'] = passages_with_facts
    if len(d['passages']) > 0:
        data_with_facts.append(d)
print(f'Document with given relations count = {len(data_with_facts)}')
print(f'Total fact count = {len(all_facts)}')


Original document count = 3977
Document with given relations count = 1117
Total fact count = 2483


In [ ]:
sub = []
for f in all_facts:
    if str(f['subjectText']).lower() not in ['i', 'my', 'he', 'she', 'his', 'her', 'who', 'myself'] and str(f['objectText']).lower() not in ['where', 'them', 'they', 'when']:
        sub.append(f['subjectText'])
print(f'Total sub count = {len(sub)}')
u_sub = list(set(sub))
u_sub.sort()
print(f'Total sub count = {len(u_sub)}')
u_sub


In [ ]:
for d in data_with_facts:
    print(f'{d["documentId"]}:')
    # print(f'{d["documentText"]}:')
    for p in d['passages']:
        print(f'\t{p["passageId"]}:')
        for f in p['facts']:
            print(f'\t\t{f["humanReadable"]}:')


In [94]:
from neo4j import GraphDatabase

# Connect to Neo4j
uri = "bolt://localhost:7687"
username = "etl_user"
password = "etl_user123"
driver = GraphDatabase.driver(uri, auth=(username, password))
session = driver.session(database="knowledgenet")

# Iterate through the folds
for fact in all_facts:
    try:
        subjectText = str(fact['subjectText']).replace("'", "\\'")
        objectText = str(fact['objectText']).replace("'", "\\'")
        relation = relations_map[int(fact['propertyId'])][1]


        query = f"MERGE (p:Person {{name: '{subjectText}'}}) \
                                ON CREATE SET p.name = '{subjectText}'"

        print(query)
        session.run(query)

        if fact['propertyId'] in ['10', '11', '12']:
            # Loc
            query = f"MERGE (p:Location {{name: '{objectText}'}}) \
                                ON CREATE SET p.name = '{objectText}'"
            session.run(query)
            # Create the  relationship
            query = f"MATCH (d:Person {{name: '{subjectText}'}}), (p:Location {{name: '{objectText}'}}) MERGE (d)-[:{relation}]->(p)"

            print(query)
            session.run(query)

        if fact['propertyId'] in ['3', '9']:
            # Org
            query = f"MERGE (p:Organization {{name: '{objectText}'}}) \
                                ON CREATE SET p.name = '{objectText}'"
            print(query)
            session.run(query)
            # Create the  relationship
            query = f"MATCH (d:Person {{name: '{subjectText}'}}), (p:Organization {{name: '{objectText}'}}) MERGE (d)-[:{relation}]->(p)"
            print(query)
            session.run(query)

        if fact['propertyId'] in ['15']:
            # Org
            query = f"MERGE (p:Date {{name: '{objectText}'}}) \
                                ON CREATE SET p.name = '{objectText}'"
            print(query)
            session.run(query)
            # Create the  relationship
            query = f"MATCH (d:Person {{name: '{subjectText}'}}), (p:Date {{name: '{objectText}'}}) MERGE (d)-[:{relation}]->(p)"
            print(query)
            session.run(query)
    except:
        print('failed to insert')

MERGE (p:Person {name: 'بد الله بن محمد بن سعود آل ثاني'})                                 ON CREATE SET p.name = 'بد الله بن محمد بن سعود آل ثاني'
MATCH (d:Person {name: 'بد الله بن محمد بن سعود آل ثاني'}), (p:Location {name: 'Qatari'}) MERGE (d)-[:NATIONALITY]->(p)
MERGE (p:Person {name: 'Abdullah bin Mohammed bin Saud Al Thani'})                                 ON CREATE SET p.name = 'Abdullah bin Mohammed bin Saud Al Thani'
MATCH (d:Person {name: 'Abdullah bin Mohammed bin Saud Al Thani'}), (p:Location {name: 'Qatari'}) MERGE (d)-[:NATIONALITY]->(p)
MERGE (p:Person {name: 'Jim Harris'})                                 ON CREATE SET p.name = 'Jim Harris'
MATCH (d:Person {name: 'Jim Harris'}), (p:Location {name: 'American'}) MERGE (d)-[:NATIONALITY]->(p)
MERGE (p:Person {name: 'James Patrick Harris'})                                 ON CREATE SET p.name = 'James Patrick Harris'
MATCH (d:Person {name: 'James Patrick Harris'}), (p:Location {name: 'American'}) MERGE (d)-[:NATIONALITY]->